In [9]:
import ibis
from ibis import _
import streamlit as st
import ibis.expr.datatypes as dt  # Make sure to import the necessary module


conn = ibis.duckdb.connect(extensions=["spatial"])

state_boundaries = "https://data.source.coop/cboettig/us-boundaries/us-state-territory.parquet"
county_boundaries = "https://data.source.coop/cboettig/us-boundaries/us-county.parquet"
states = conn.read_parquet(state_boundaries).rename(state_id = "STUSPS", state = "NAME")
county = conn.read_parquet(county_boundaries).rename(county = "NAMELSAD", state = "STATE_NAME")

localities_boundaries = "us_localities.parquet"
locality = conn.read_parquet(localities_boundaries)


votes = conn.read_csv("landvote.csv")

In [10]:
vote_county = (votes
                .filter(_["Jurisdiction Type"] == "County")
                .rename(county = "Jurisdiction Name", state_id = "State")
                .mutate(key = _.county + ibis.literal('-') + _.state_id)
                .rename(amount = 'Conservation Funds at Stake', yes = '% Yes')
                .mutate(amount_n=_.amount.replace('$', '').replace(',', '').cast('float'))
                .mutate(log_amount=_.amount_n.log())
                .mutate(year=_['Date'].year().cast('int32'))
                .mutate(
                    yes=ibis.case()
                        .when(_.yes.isin(['Pass', 'None','Fail']), None)  # Handle non-numeric cases
                        .when(_.yes.notnull(), (_.yes.replace('%', '').cast('float').round(2).cast(dt.float64)).cast(dt.string) + '%')  # Convert valid percentages and add %
                        .else_(None)  # Default to None for other cases
                        .end()
                )
               .mutate(log_amount = _.log_amount.round(4))
                .select('key', 'Status', 'yes', 'year', 'amount', 'log_amount', )
               )
df_county = (county
            .join(states.select("state", "state_id"), "state")
            .mutate(key = _.county + ibis.literal('-') + _.state_id)
            .select('key', 'geometry')
            .right_join(vote_county, "key")
            .drop('key_right')
            .mutate(jurisdiction = ibis.literal("County"))
            .cast({"geometry": "geometry"})
             )


In [11]:
vote_local = (votes
                .filter(_["Jurisdiction Type"] == "Municipal")
                .rename(city = "Jurisdiction Name", state_id = "State")
                .mutate(key = _.city + ibis.literal('-') + _.state_id)
                .rename(amount = 'Conservation Funds at Stake', yes = '% Yes')
                .mutate(amount_n=_.amount.replace('$', '').replace(',', '').cast('float'))
                .mutate(log_amount=_.amount_n.log())
                .mutate(year=_['Date'].year().cast('int32'))
                .mutate(
                    yes=ibis.case()
                        .when(_.yes.isin(['Pass', 'None','Fail']), None)  # Handle non-numeric cases
                        .when(_.yes.notnull(), (_.yes.replace('%', '').cast('float').round(2).cast(dt.float64)).cast(dt.string) + '%')  # Convert valid percentages and add %
                        .else_(None)  # Default to None for other cases
                        .end()
                )
              .mutate(log_amount = _.log_amount.round(4))
                .select('key', 'Status', 'yes', 'year', 'amount', 'log_amount', )
                )

df_local = (locality
            .mutate(key = _.name + ibis.literal('-') + _.state_id)
            .select('key', 'geometry')
            .right_join(vote_local, "key")
            .drop('key_right')
            .mutate(jurisdiction = ibis.literal("Municipal"))
            .cast({"geometry": "geometry"})
            .mutate(geometry = _.geometry.buffer(.07))
            )


In [12]:
df = df_county.union(df_local)
# df.execute()

In [13]:
import subprocess
import os
from huggingface_hub import HfApi, login
import streamlit as st

login(st.secrets["HF_TOKEN"])
# api = HfApi(add_to_git_credential=False)
api = HfApi()

def hf_upload(file, repo_id):
    info = api.upload_file(
            path_or_fileobj=file,
            path_in_repo=file,
            repo_id=repo_id,
            repo_type="dataset",
        )
def generate_pmtiles(input_file, output_file, max_zoom=12):
    # Ensure Tippecanoe is installed
    if subprocess.call(["which", "tippecanoe"], stdout=subprocess.DEVNULL) != 0:
        raise RuntimeError("Tippecanoe is not installed or not in PATH")

    # Construct the Tippecanoe command
    command = [
        "tippecanoe",
        "-o", output_file,
        "-zg",
        "--extend-zooms-if-still-dropping",
        "--force",
        "--projection", "EPSG:4326",  
        input_file
    ]

    # Run Tippecanoe
    try:
        subprocess.run(command, check=True)
        print(f"Successfully generated PMTiles file: {output_file}")
    except subprocess.CalledProcessError as e:
        print(f"Error running Tippecanoe: {e}")



The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `huggingface-cli` if you want to set the git credential as well.
Token is valid (permission: write).
Your token has been saved to /home/rstudio/.cache/huggingface/token
Login successful


In [14]:
gdf= df.execute()
gdf = gdf.set_crs("EPSG:4326")
# print(gdf.crs)
# gdf.to_parquet("votes.parquet")

gdf.to_file("vote.geojson")
hf_upload("vote.geojson", "boettiger-lab/landvote")

generate_pmtiles("vote.geojson", "vote.pmtiles")
hf_upload("vote.pmtiles", "boettiger-lab/landvote")



FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

vote.geojson:   0%|          | 0.00/92.9M [00:00<?, ?B/s]

For layer 0, using name "vote"
vote.geojson:496: null geometry (additional not reported): in JSON object {"type":"Feature","properties":{"key":null,"Status":"Fail","yes":"43.67%","year":1990,"amount":null,"log_amount":null,"jurisdiction":"County"},"geometry":null}
2195 features, 10746823 bytes of geometry and attributes, 58352 bytes of string pool, 0 bytes of vertices, 0 bytes of nodes
Choosing a maxzoom of -z3 for features typically 81840 feet (24945 meters) apart, and at least 10982 feet (3348 meters) apart
Choosing a maxzoom of -z11 for resolution of about 214 feet (65 meters) within features
  99.9%  11/189/562  


Successfully generated PMTiles file: vote.pmtiles


vote.pmtiles:   0%|          | 0.00/4.81M [00:00<?, ?B/s]

In [15]:
import leafmap.maplibregl as leafmap
m = leafmap.Map(style="positron")

url = "https://huggingface.co/datasets/boettiger-lab/landvote/resolve/main/vote.pmtiles"

outcome = [
      'match',
      ['get', 'Status'], 
      "Pass", '#2E865F',
      "Fail", '#FF3300', 
      '#ccc'
    ]
paint = {"fill-extrusion-color": outcome, 
         "fill-extrusion-opacity": 0.7,
         "fill-extrusion-height": ["*", ["get", "log_amount"], 5000],
        }
style = {
    "layers": [
        {
            "id": "votes",
            "source": "vote",
            "source-layer": "vote",
            "type": "fill-extrusion",
            "filter": [
                "==",
                ["get", "year"],
                2022,
            ],  # only show buildings with height info
            "paint": paint
        },
    ],
}

m.add_pmtiles(
    url,
    style=style,
    visible=True,
    opacity=1.0,
    tooltip=True,
    fit_bounds=False,
)

m



Map(height='600px', map_options={'bearing': 0, 'center': (0, 20), 'pitch': 0, 'style': 'https://basemaps.carto…